In [7]:
#Import Libraries
from selenium import webdriver
from selenium.webdriver.support.ui import Select
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.common.exceptions import NoSuchElementException,TimeoutException
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import StaleElementReferenceException
import pandas as pd
import lxml
import os
import time
import datetime
import json

In [8]:
#Start Timmer
start = time.time()

#Set Output Folder
output_folder = datetime.datetime.now().strftime("Date-%Y-%m-%d-Time-%H-%M-%S")
if not os.path.exists(output_folder):
    os.makedirs(output_folder)

In [9]:
#Start Chrome
driver = webdriver.Chrome()
driver.implicitly_wait(20) # seconds

#Prepare URL
protocol = "https://"
url = protocol + "rhreporting.nic.in/netiay/FinancialProgressReport/finProgress_newRpt.aspx"
params = {
    'params': 0
}
for key, value in params.items():
    url = url #+ "&" + key + "=" + str(value)

#Playing with headers
my_referer = url
UserAgent = 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_10_1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/39.0.2171.95 Safari/537.36'
mod_headers = {'referer': my_referer, 'User-Agent':UserAgent}

#Start Chrome
driver.get(url)

In [10]:
# Select List
year_select_name = 'ctl00$ContentPlaceHolder1$ddl_finYear'
iay_radio_name = 'ctl00$ContentPlaceHolder1$rdlScheme'
excel_button = 'ctl00$ContentPlaceHolder1$btnExport'
content_table_class = 'table_s'

In [11]:
#Build State List
def build_list(element_name):
    temp_list = driver.find_element_by_name(element_name).find_elements_by_xpath(".//option")[1:]
    _list = []
    #loop over each option
    for x in temp_list:
        d = {}
        d['text'] = x.text
        d['value'] = x.get_attribute('value')
        _list.append(d)
        #print("_list index:",i,d)
    return _list

def check_table():
    #Wait for Table to Load fully
    element_present = EC.presence_of_element_located((By.CSS_SELECTOR, '.'+content_table_class))            
    WebDriverWait(driver, 2).until(element_present)
    
#Check Submit button
def delete_excel():
    driver.execute_script("return document.getElementsByName('" + excel_button + "')[0].remove()")
def check_excel():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.NAME, excel_button ) ) )

In [12]:
#Start Chrome
driver.get(url)
element = WebDriverWait(driver, 10).until(
    EC.element_to_be_clickable((By.NAME, year_select_name))
)
element.find_element_by_xpath(".//option[@value='0']").click()
yearlist = build_list(year_select_name)[4:5]
print(yearlist)
for year in yearlist:
    print("--Scrapping data for Year: ", year['text'])
    #Start Chrome
    driver.get(url)
    #Year Selection
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, year_select_name))
    )
    element.find_element_by_xpath(".//option[@value='0']").click()
    year_query = ".//option[@value='" + year['value'] + "']"
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, year_select_name))
    )
    element.find_element_by_xpath(year_query).click()
    
    #DataStore
    df_list = []
    
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, iay_radio_name))
    )
    element.click()
    
    #state select
    check_table()
    temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[3:-2]
    states = []
    for row in temp_list:
        try:
            x = {}
            td = row.find_elements_by_xpath(".//td")[1]
            x['name'] = td.text
            x['link'] = td.find_element_by_tag_name("a").get_attribute("href")
            states.append(x)
        except Exception as e:
            print("Error while parsing table data |", e)
    for state in states:
        print("----Scrapping data for State: ", state['name'])
        driver.get(state['link'])
        check_table()
        temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[4:-1]
        districts = []
        for row in temp_list:
            x = {}            
            x['name'] = row.find_elements_by_xpath(".//td")[1].text
            x['link'] =row.find_elements_by_xpath(".//td")[1].find_element_by_tag_name("a").get_attribute("href")
            districts.append(x)
        for district in districts:
            print("------Scrapping data for District: ", district['name'])
            driver.get(district['link'])
            check_table()
            temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[4:-1]
            blocks = []
            for row in temp_list:
                x = {}            
                x['name'] = row.find_elements_by_xpath(".//td")[1].text
                x['link'] =row.find_elements_by_xpath(".//td")[1].find_element_by_tag_name("a").get_attribute("href")
                blocks.append(x)
            
            for block in blocks:
                print("--------Scrapping data for Block: ", block['name'])
                driver.get(block['link'])
                check_table()
                html_table = driver.find_element_by_class_name(content_table_class).get_attribute('outerHTML')
                df = pd.read_html(html_table, header=3)[0]
                df = df[:-1]
                #df.columns = table_head
                df['Financial Year'] = year['text']
                df['State Name'] = state['name']
                df['District Name'] = district['name']
                df['Block Name'] = block['name']
                df_list.append(df)
                #except Exception as e:
                #    print("Error while table data |", e)
                
    #merge all dataframes to master dataframe
    df = pd.concat(df_list)
    df.drop(df.columns[0],axis=1,inplace=True)
    df = df.reset_index()
    #Save Scrapped File
    df.to_csv(os.path.join(output_folder, year['text']+'_Scrapped_Data.csv'), encoding='utf-8', index=False)

[{'text': '2014-2015', 'value': '2014-2015 '}]
--Scrapping data for Year:  2014-2015
Error while parsing table data | Message: no such element: Unable to locate element: {"method":"tag name","selector":"a"}
  (Session info: chrome=66.0.3359.181)
  (Driver info: chromedriver=2.35.528161 (5b82f2d2aae0ca24b877009200ced9065a772e73),platform=Windows NT 10.0.17134 x86_64)

----Scrapping data for State:  ARUNACHAL PRADESH
------Scrapping data for District:  LOHIT
--------Scrapping data for Block:  CHONGKHAM
------Scrapping data for District:  LOWER DIBANG VALLEY
--------Scrapping data for Block:  DUMBUK-PAGLAM
--------Scrapping data for Block:  HUNLI-DESALI
--------Scrapping data for Block:  ROING-KORONU
------Scrapping data for District:  LOWER SUBANSIRI
--------Scrapping data for Block:  RAGA
--------Scrapping data for Block:  ZIRO-I
--------Scrapping data for Block:  ZIRO-II
------Scrapping data for District:  TAWANG
--------Scrapping data for Block:  TAWANG
----Scrapping data for State:  

--------Scrapping data for Block:  GHILAMARA
--------Scrapping data for Block:  KARUNABARI
--------Scrapping data for Block:  LAKHIMPUR
--------Scrapping data for Block:  NARAYANPUR
--------Scrapping data for Block:  NOWBOICHA
--------Scrapping data for Block:  TELAHI
------Scrapping data for District:  Morigaon
--------Scrapping data for Block:  BHURBANDHA
--------Scrapping data for Block:  KAPILI
--------Scrapping data for Block:  LAHARIGHAT
--------Scrapping data for Block:  MAYONG
--------Scrapping data for Block:  MOIRABARI
------Scrapping data for District:  NAGAON
--------Scrapping data for Block:  Bajiagaon
--------Scrapping data for Block:  Barhampur
--------Scrapping data for Block:  Batadraba
--------Scrapping data for Block:  Binakandi
--------Scrapping data for Block:  Dhalpukhuri
--------Scrapping data for Block:  Dolongghat
--------Scrapping data for Block:  Jugijan
--------Scrapping data for Block:  Juria
--------Scrapping data for Block:  Kaliabor
--------Scrapping dat

--------Scrapping data for Block:  CHAUSA
--------Scrapping data for Block:  CHOUGAI
--------Scrapping data for Block:  DUMRAON
--------Scrapping data for Block:  ITARHI
--------Scrapping data for Block:  KESATH
--------Scrapping data for Block:  NAWANAGAR
--------Scrapping data for Block:  RAJPUR
--------Scrapping data for Block:  SIMRI
------Scrapping data for District:  DARBHANGA
--------Scrapping data for Block:  ALINAGAR
--------Scrapping data for Block:  BAHADURPUR
--------Scrapping data for Block:  BAHERI
--------Scrapping data for Block:  BENIPUR
--------Scrapping data for Block:  BIRAUL
--------Scrapping data for Block:  DARBHANGA
--------Scrapping data for Block:  GAURABAURAM
--------Scrapping data for Block:  GHANSHYAMPUR
--------Scrapping data for Block:  HANUMAN NAGAR
--------Scrapping data for Block:  HAYAGHAT
--------Scrapping data for Block:  JALE
--------Scrapping data for Block:  KEOTIRUNWAY
--------Scrapping data for Block:  KIRATPUR
--------Scrapping data for Block:

--------Scrapping data for Block:  AURAI
--------Scrapping data for Block:  Bandra
--------Scrapping data for Block:  BOCHAHAN
--------Scrapping data for Block:  GAIGHAT
--------Scrapping data for Block:  KANTI
--------Scrapping data for Block:  KATRA
--------Scrapping data for Block:  KURHANI
--------Scrapping data for Block:  MARWAN
--------Scrapping data for Block:  MINAPUR
--------Scrapping data for Block:  MOTIPUR
--------Scrapping data for Block:  MURAUL
--------Scrapping data for Block:  MUSHAHARI
--------Scrapping data for Block:  PAROO
--------Scrapping data for Block:  SAHEBGANJ
--------Scrapping data for Block:  Sakra
--------Scrapping data for Block:  SARAIYA
------Scrapping data for District:  NALANDA
--------Scrapping data for Block:  ASTHAWAN BLOCK
--------Scrapping data for Block:  BEN
--------Scrapping data for Block:  BIHARSARIF
--------Scrapping data for Block:  BIND BLOCK
--------Scrapping data for Block:  CHANDI BLOCK
--------Scrapping data for Block:  EKANGARSARAI

--------Scrapping data for Block:  EKMA
--------Scrapping data for Block:  GARKHA
--------Scrapping data for Block:  ISUAPUR
--------Scrapping data for Block:  JALALPUR
--------Scrapping data for Block:  LAHLADPUR
--------Scrapping data for Block:  MAKER
--------Scrapping data for Block:  MANJHI
--------Scrapping data for Block:  MARHAURA
--------Scrapping data for Block:  MASHRAKH
--------Scrapping data for Block:  NAGRA
--------Scrapping data for Block:  PANAPUR
--------Scrapping data for Block:  PARSA
--------Scrapping data for Block:  REVELGANJ
--------Scrapping data for Block:  SONEPUR
--------Scrapping data for Block:  TARAIYA
------Scrapping data for District:  Sheikhpura
--------Scrapping data for Block:  ARIARI
--------Scrapping data for Block:  BARBHIGA
--------Scrapping data for Block:  CHEWARA
--------Scrapping data for Block:  GHAT KHUSUMBAHA
--------Scrapping data for Block:  SHEIKHPURA
--------Scrapping data for Block:  SHEOKHOPUR SARAI
------Scrapping data for District:

...

--------Scrapping data for Block:  Parchur
--------Scrapping data for Block:  Pedaaraveedu
--------Scrapping data for Block:  Pedacherlopalle
--------Scrapping data for Block:  Podili
--------Scrapping data for Block:  Ponnaluru
--------Scrapping data for Block:  Pullalacheruvu
--------Scrapping data for Block:  Racherla
--------Scrapping data for Block:  Santhamaguluru
--------Scrapping data for Block:  Santhanuthlapadu
--------Scrapping data for Block:  Singarayakonda
--------Scrapping data for Block:  Tangutur
--------Scrapping data for Block:  Tarlapadu
--------Scrapping data for Block:  Thallur
--------Scrapping data for Block:  Tripuranthakam
--------Scrapping data for Block:  Ulavapadu
--------Scrapping data for Block:  Veligandla
--------Scrapping data for Block:  Vetapalem
--------Scrapping data for Block:  Voletivaripalem
--------Scrapping data for Block:  Yeddanapudi
--------Scrapping data for Block:  Yerragondapalem
--------Scrapping data for Block:  Zarugumilli
------Scrap

--------Scrapping data for Block:  Undrajavaram
--------Scrapping data for Block:  Unguturu
--------Scrapping data for Block:  Veeravasaram
--------Scrapping data for Block:  Yelamanchili
----Scrapping data for State:  KARNATAKA
------Scrapping data for District:  Bagalkot
--------Scrapping data for Block:  Badami
--------Scrapping data for Block:  Bagalkot
--------Scrapping data for Block:  Bilagi
--------Scrapping data for Block:  Hunugund
--------Scrapping data for Block:  Jamakhandi
--------Scrapping data for Block:  Mudhol
------Scrapping data for District:  Ballari
--------Scrapping data for Block:  Ballari
--------Scrapping data for Block:  Hadagali
--------Scrapping data for Block:  Hagaribommanahalli
--------Scrapping data for Block:  Hosapete
--------Scrapping data for Block:  Kudligi
--------Scrapping data for Block:  Sandur
--------Scrapping data for Block:  Siruguppa
------Scrapping data for District:  Belagavi
--------Scrapping data for Block:  Athani
--------Scrapping da

--------Scrapping data for Block:  Tiptur
--------Scrapping data for Block:  Tumakuru
--------Scrapping data for Block:  Turuvekere
------Scrapping data for District:  Udupi
--------Scrapping data for Block:  Karkala
--------Scrapping data for Block:  Kundapura
--------Scrapping data for Block:  Udupi
------Scrapping data for District:  UttaraKannada
--------Scrapping data for Block:  Ankola
--------Scrapping data for Block:  Bhatkal
--------Scrapping data for Block:  Haliyal
--------Scrapping data for Block:  Honnavar
--------Scrapping data for Block:  Joida
--------Scrapping data for Block:  Karwar
--------Scrapping data for Block:  Kumta
--------Scrapping data for Block:  Mundgod
--------Scrapping data for Block:  Siddapura
--------Scrapping data for Block:  Sirsi
--------Scrapping data for Block:  Yellapura
------Scrapping data for District:  Vijayapura
--------Scrapping data for Block:  Basavana Bagewadi
--------Scrapping data for Block:  Indi
--------Scrapping data for Block:  Mu

--------Scrapping data for Block:  ACHAMPETA
--------Scrapping data for Block:  ADDAKAL
--------Scrapping data for Block:  AIZA
--------Scrapping data for Block:  ALAMPUR
--------Scrapping data for Block:  AMANGAL
--------Scrapping data for Block:  AMRABAD
--------Scrapping data for Block:  ATMAKUR
--------Scrapping data for Block:  BALANAGAR
--------Scrapping data for Block:  BALMOOR
--------Scrapping data for Block:  BHOOTHPUR
--------Scrapping data for Block:  BIJINAPALLE
--------Scrapping data for Block:  BOMRASPETA
--------Scrapping data for Block:  CHINNA CHINTA KUNTA
--------Scrapping data for Block:  DAMARAGIDDA
--------Scrapping data for Block:  DEVARKADARA
--------Scrapping data for Block:  DHANWADA
--------Scrapping data for Block:  DHARUR
--------Scrapping data for Block:  DOULATABAD
--------Scrapping data for Block:  FAROOQNAGAR
--------Scrapping data for Block:  GADWAL
--------Scrapping data for Block:  GHANPUR
--------Scrapping data for Block:  GHATTU
--------Scrapping d

--------Scrapping data for Block:  GANDHARI
--------Scrapping data for Block:  JAKRANPALLE
--------Scrapping data for Block:  JUKKAL
--------Scrapping data for Block:  KAMAREDDY
--------Scrapping data for Block:  KAMMAR PALLE
--------Scrapping data for Block:  KOTGIRI
--------Scrapping data for Block:  LINGAMPET
--------Scrapping data for Block:  MACHAREDDY
--------Scrapping data for Block:  MADNUR
--------Scrapping data for Block:  MAKLOOR
--------Scrapping data for Block:  MORTAD
--------Scrapping data for Block:  NAGA REDDIPET
--------Scrapping data for Block:  NANDIPET
--------Scrapping data for Block:  NAVIPET
--------Scrapping data for Block:  NIZAM SAGAR
--------Scrapping data for Block:  NIZAMABAD
--------Scrapping data for Block:  PITLAM
--------Scrapping data for Block:  RANJAL
--------Scrapping data for Block:  SADASIVANAGAR
--------Scrapping data for Block:  SIRKONDA
--------Scrapping data for Block:  TADWAI
--------Scrapping data for Block:  VARNI
--------Scrapping data fo